## Data Pipeline

In [ ]:
from pyspark.sql.functions import col

#pulling external data 
import requests 
import io
import pandas as pd

from operator import add 


import pandas as pd

#pulling out values from string column
from pyspark.sql.functions import substring, concat, to_timestamp,lit, expr, lpad, when, length, date_format,count,col, udf,  unix_timestamp, concat, to_utc_timestamp, to_date, count, col, when

from pyspark.sql import Row


from pyspark.sql import functions as F
#
# from pyspark_dist_explore import hist #!pip install pyspark-dist-explore
import matplotlib.pyplot as plt

import numpy as np 
from pandas import DataFrame
import seaborn as sns
%matplotlib inline


# for time conversion
import datetime
import pytz
#from tzwhere import tzwhere # !pip install tzwhere
import time 


#categorical indexer
from pyspark.ml.feature import StringIndexer

# NOTE: FOLLOWING MIGHT HAVE SOME REPEATING LIBRARIES; TODO:
from pyspark.ml.linalg import DenseVector, SparseVector, Vectors
from pyspark.ml.feature import VectorAssembler, StandardScaler

from pyspark.ml import Pipeline
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
#to reload the model
# from pyspark.ml.regression import RandomForestRegressionModel
from pyspark.ml.tuning import CrossValidatorModel # should be using cv to fine tune, so use this one 



In [ ]:
# storage blob link
store_blob_url = f"dbfs:/FileStore/shared_uploads/lingyue@berkeley.edu"


# Expected input data for this notebook:
The input to this notebook would be a dataframe that has the joined flights and weather tables' data. We will read that data in and make our feature engineered features.

The notebook used to create our joined data is here: https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/3035635552860035/command/3035635552860036

# Phase 3 Feature Engineering
* Convert all time to udf to derive the time relevant features 
* Derived features we plan to use
  * Implementation: page rank (delay rank of destination and departure airport), count of flights delayed on that day at the departure airport, holiday flags
## Note: there are checkpoint blobs in some cells below, don't need to run all cells

In [ ]:
join_df = spark.read.parquet(f"{store_blob_url}/final_join_2_nonull")
# display(join_df.head(2))

## Data cleaning from previous phases
* was done here: https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/2647101326220280/command/2647101326220281

## Make udf function to convert time zone to utc

In [ ]:
def utc_departure(departName, depart2hrGapName, origDepartCol, origDepart2hrEarlyCol, df, timezone):
    '''
      convert the flight departure time and the hour before departure time to utc so that the feature engineered features can be consistent across all flights.
      departName - string; column name of the newly created column of utc departure 
      depart2hrGapName - string; column name of the newly created column of 2 hours before utc departure
      origDepartCol - string; column name of the original column that contains the departure flight local time 
      origDepart2hrEarlyCol - string; column name of the original column that contains the 2 hour before departure flight local time 
      df - pyspark dataframe; original data from the joined and cleaned notebooks
      timezone - string; column name from the original dataframe that holds the timezone of the flight departure airport
      
    '''
    df = df.withColumn(departName, to_utc_timestamp(df[origDepartCol], df[timezone]))
    # would need the 2 hr before utc to make sure no data leakage in our delay count feature engineered feature
    df = df.withColumn(depart2hrGapName, to_utc_timestamp(df[origDepart2hrEarlyCol], df[timezone]))        
    return df

In [ ]:
join_df = utc_departure('DepartureUTC', 'DepartureUTC2', 'ORIGIN_TIMESTAMP', 'ORIGIN_TIMESTAMP2', join_df, 'AIRPORT_TIMEZONE')

In [ ]:
join_df.display()

STATION AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed DepartureUTC DepartureUTC2 72202012839 America/New_York 25.79325 -80.29055556 N3JAAA AA 2016-03-13 2016-03-13T14:09:00.000+0000 2016-03-13T12:09:00.000+0000 2016 1 3 13 7 MIA LGA 1409 171.0 12953 AA 310 1400-1459 1700-1759 1700 0.0 0.0 5.0 13303 76.27777777777777 77.16666666666667 9.986666666666666 144.44444444444446 10.166666666666666 2016-03-13T18:09:00.000+0000 2016-03-13T16:09:00.000+0000 72205012815 America/New_York 28.42888889 -81.31602778 N421LV WN 2017-09-15 2017-09-15T15:10:00.000+0000 2017-09-15T13:10:00.000+0000 2017 3 9 15 5 MCO IND 1510 135.0 12339 WN 798 1500-1559 1700-1759 1725 0.0 0.0 -7.0 13204 76.4 94.13333333333334 9.991999999999999 50.666666666666664 2.6666666666666665 2017-09-15T19:10:00.000+0000 2017-09-15T17:10:00.000+0000 72205012815 America/New_York 28.42888889 -81.31602778 N812DN DL 2021-04-13 00:00:00 2021-04-13T11:00:00.000+0000 2021-04-13T09:00:00.000+0000 2021 2 4 13 2 MCO SLC 1100 292.0 14869 DL 532 1100-1159 1300-1359 1352 0.0 0.0 -5.0 13204 64.0 82.81818181818181 9.989090909090908 140.9090909090909 2.1818181818181817 2021-04-13T15:00:00.000+0000 2021-04-13T13:00:00.000+0000 72211012842 America/New_York 27.97547222 -82.53325 N927DA DL 2016-07-04 2016-07-04T18:56:00.000+0000 2016-07-04T16:56:00.000+0000 2016 3 7 4 1 TPA ATL 1856 101.0 10397 DL 2081 1800-1859 2000-2059 2037 0.0 0.0 -5.0 15304 85.69565217391305 73.0 9.984347826086957 123.91304347826087 4.6521739130434785 2016-07-04T22:56:00.000+0000 2016-07-04T20:56:00.000+0000 72211012842 America/New_York 27.97547222 -82.53325 N309DN DL 2017-02-03 2017-02-03T14:50:00.000+0000 2017-02-03T12:50:00.000+0000 2017 1 2 3 5 TPA ATL 1450 97.0 10397 DL 2330 1400-1459 1600-1659 1627 0.0 0.0 4.0 15304 62.0 76.71428571428571 9.987142857142857 118.57142857142857 3.7142857142857144 2017-02-03T19:50:00.000+0000 2017-02-03T17:50:00.000+0000 72222313899 America/Chicago 30.47330556 -87.18744444 N928DL DL 2017-04-02 2017-04-02T09:20:00.000+0000 2017-04-02T07:20:00.000+0000 2017 2 4 2 7 PNS ATL 920 70.0 10397 DL 2212 0900-0959 1100-1159 1130 0.0 0.0 -10.0 14193 65.375 90.0 7.25 42.5 3.125 2017-04-02T14:20:00.000+0000 2017-04-02T12:20:00.000+0000 72228013876 America/Chicago 33.56294306 -86.75354972 N559NN OH 2021-08-24 00:00:00 2021-08-24T07:28:00.000+0000 2021-08-24T05:28:00.000+0000 2021 3 8 24 2 BHM CLT 728 96.0 11057 OH 5228 0700-0759 1000-1059 1004 0.0 0.0 -10.0 10599 73.4 87.6 9.6 0.0 0.0 2021-08-24T12:28:00.000+0000 2021-08-24T10:28:00.000+0000 72243012960 America/Chicago 29.98047222 -95.33972222 N431UA UA 2016-01-22 2016-01-22T19:27:00.000+0000 2016-01-22T17:27:00.000+0000 2016 1 1 22 5 IAH DEN 1927 161.0 11292 UA 1876 1900-1959 2100-2159 2108 0.0 0.0 2.0 12266 44.68181818181818 57.13636363636363 9.991818181818182 320.45454545454544 18.09090909090909 2016-01-23T01:27:00.000+0000 2016-01-22T23:27:00.000+0000 72243012960 America/Chicago 29.98047222 -95.33972222 N16709 UA 2018-07-10 2018-07-10T09:35:00.000+0000 2018-07-10T07:35:00.000+0000 2018 3 7 10 2 IAH MIA 935 158.0 13303 UA 1994 0900-0959 1300-1359 1313 0.0 0.0 5.0 12266 74.5 100.0 9.664 73.0 1.6 2018-07-10T14:35:00.000+0000 2018-07-10T12:35:00.000+0000 72243012960 America/Chicago 29.98047222 -95.33972222 N25134 EV 2019-02-25 2019-02-25T18:20:00.000+0000 2019-02-25T16:20:00.000+0000 2019 1 2 25 1 IAH HOB 1820 110.0 12177 EV 4442 1800-1859 1900-1959 1910 1.0 0.0 82.0 12266 53.77272727272727 56.5 9.991818181818182 80.9090909090909 8.772727272727273 2019-02-26T00:20:00.000+0000 2019-02-25T22:20:00.000+0000 72243012960 America/Chicago 29.98047222 -95.33972222 N886NN AA 2019-05-07 2019-05-07T18:24:00.000+0

# Phase 3 derived feature
We will derive 2 more features to our model. We would like to make a feature that is a flag set for each airport if there's any delay. For example, if there's a delay for flight A, then we will set a flag for that airport until the delay has passed. Another feature we would be interested in relates to finding out specific carriers that are delayed. This may give better predictions as some airlines may be more susceptible to delays or if X airline is delayed at city A, this might impact their schedule for other cities as well. So we will set a flag as to an airline that's delayed to other cities of the same time frame until the delay has passed.
* the flags will be a start time (1 column) and an end time (1 column) of when the delays are happening for either that airport or that carrier
* can also vary the above based on the source or the destination airport

In [ ]:
# create a new column "delayed departure time": if there's a delay, add "DEP_DELAY" to "DepartureUTC" , else "FlightDepartTimeStamp". The derived feature will check if there are delays at that airport at that time. 
# NOTE: THIS IS NOT A FEATURE TO BE USED IN THE PREDICTION, JUST used for building the derived feature 

def delayedAirportTime(delayIndicator, srcAirport):
    if delayIndicator:
        delAirport = srcAirport
    else:
        delAirport = 'notDelayed'
    return (delAirport) 


def delayedDate(delayIndicator, Date):
    if delayIndicator:
        return (Date)
    else:
        return None
     
def delayedStart(delayIndicator, originFlightDepart):
    if delayIndicator :
        #only want the delayed minutes if they are non-nulls. else assume no delays
        if originFlightDepart:
            return str(originFlightDepart )
    else:
        return None

    
delayedAirportUDF = udf(lambda delInd, srcAirport: delayedAirportTime(delInd, srcAirport))    
delayedDateUDF = udf(lambda delInd, delDate: delayedDate(delInd, delDate))   
delayedStartUDF = udf(lambda delInd, flightDepTime: delayedStart(delInd, flightDepTime))    


join_df = join_df.withColumn("airportDelayed", delayedAirportUDF(join_df.DEP_DEL15, join_df.ORIGIN))

join_df = join_df.withColumn("dateDelayed", delayedDateUDF(join_df.DEP_DEL15, join_df.FL_DATE))

join_df = join_df.withColumn("timeStartDelayed", unix_timestamp(delayedStartUDF(join_df.DEP_DEL15, join_df.DepartureUTC)).cast("timestamp"))


## Count number of delays happening that day at the airport

In [ ]:
#create temporary tables for queries and joining
join_df.registerTempTable("join_df")

query = '''
SELECT *
FROM join_df  table1
LEFT JOIN join_df table2
ON table1.ORIGIN = table2.ORIGIN AND table1.DepartureUTC <= table2.DepartureUTC2
    AND table2.airportDelayed != 'notDelayed' AND table1.FL_DATE == table2.FL_DATE
'''

all_data = spark.sql(query)
display(all_data)

/databricks/spark/python/pyspark/sql/dataframe.py:234: FutureWarning: Deprecated in 2.0, use createOrReplaceTempView instead.
  warnings.warn("Deprecated in 2.0, use createOrReplaceTempView instead.", FutureWarning)


STATION AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed DepartureUTC DepartureUTC2 airportDelayed dateDelayed timeStartDelayed STATION AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed DepartureUTC DepartureUTC2 airportDelayed dateDelayed timeStartDelayed 72365023050 America/Denver 35.04022222 -106.6091944 N3ADAA AA 2017-12-31 2017-12-31T07:05:00.000+0000 2017-12-31T05:05:00.000+0000 2017 4 12 31 7 ABQ ORD 705 176.0 13930 AA 1072 0700-0759 1100-1159 1101 0.0 0.0 -4.0 10140 35.857142857142854 20.857142857142858 9.982857142857142 145.71428571428572 8.571428571428571 2017-12-31T14:05:00.000+0000 2017-12-31T12:05:00.000+0000 notDelayed null null 72365023050 America/Denver 35.04022222 -106.6091944 N7739A WN 2017-12-31 2017-12-31T20:30:00.000+0000 2017-12-31T18:30:00.000+0000 2017 4 12 31 7 ABQ PHX 2030 75.0 14107 WN 4162 2000-2059 2100-2159 2145 1.0 0.0 76.0 10140 44.65217391304348 17.08695652173913 9.984347826086957 120.43478260869566 5.0 2018-01-01T03:30:00.000+0000 2018-01-01T01:30:00.000+0000 ABQ 2017-12-31 2018-01-01T03:30:00.000+0000 72365023050 America/Denver 35.04022222 -106.6091944 N3ADAA AA 2017-12-31 2017-12-31T07:05:00.000+0000 2017-12-31T05:05:00.000+0000 2017 4 12 31 7 ABQ ORD 705 176.0 13930 AA 1072 0700-0759 1100-1159 1101 0.0 0.0 -4.0 10140 35.857142857142854 20.857142857142858 9.982857142857142 145.71428571428572 8.571428571428571 2017-12-31T14:05:00.000+0000 2017-12-31T12:05:00.000+0000 notDelayed null null 72365023050 America/Denver 35.04022222 -106.6091944 N720WN WN 2017-12-31 2017-12-31T13:20:00.000+0000 2017-12-31T11:20:00.000+0000 2017 4 12 31 7 ABQ DAL 1320 100.0 11259 WN 3886 1300-1359 1600-1659 1600 1.0 0.0 95.0 10140 38.733333333333334 20.266666666666666 9.984 123.33333333333333 5.666666666666667 2017-12-31T20:20:00.000+0000 2017-12-31T18:20:00.000+0000 ABQ 2017-12-31 2017-12-31T20:20:00.000+0000 72365023050 America/Denver 35.04022222 -106.6091944 N3ADAA AA 2017-12-31 2017-12-31T07:05:00.000+0000 2017-12-31T05:05:00.000+0000 2017 4 12 31 7 ABQ ORD 705 176.0 13930 AA 1072 0700-0759 1100-1159 1101 0.0 0.0 -4.0 10140 35.857142857142854 20.857142857142858 9.982857142857142 145.71428571428572 8.571428571428571 2017-12-31T14:05:00.000+0000 2017-12-31T12:05:00.000+0000 notDelayed null null 72365023050 America/Denver 35.04022222 -106.6091944 N962WN WN 2017-12-31 2017-12-31T11:45:00.000+0000 2017-12-31T09:45:00.000+0000 2017 4 12 31 7 ABQ DAL 1145 95.0 11259 WN 3477 1100-1159 1400-1459 1420 1.0 0.0 55.0 10140 36.25 21.916666666666668 9.985 105.83333333333333 6.0 2017-12-31T18:45:00.000+0000 2017-12-31T16:45:00.000+0000 ABQ 2017-12-31 2017-12-31T18:45:00.000+0000 72365023050 America/Denver 35.04022222 -106.6091944 N3ADAA AA 2017-12-31 2017-12-31T07:05:00.000+0000 2017-12-31T05:05:00.000+0000 2017 4 12 31 7 ABQ ORD 705 176.0 13930 AA 1072 0700-0759 1100-1159 1101 0.0 0.0 -4.0 10140 35.857142857142854 20.857142857142858 9.982857142857142 145.71428571428572 8.571428571428571 2017-12-31T14:05:00.000+0000 2017-12-31T12:05:00.000+0000 notDelayed null null 72365023050 America/Denver 35.04022222 -106.6091944 N7746C WN 2017-12-31 2017-12-31T16:30:00.000+0000 2017-12-31T14:30:00.000+0000 2017 4 12 31 7 ABQ DAL 1630 100.0 11259 WN 3106 1600-1659 1900-1959 1910 1.0 0.0 106.0 10140 41.611111111111114 18.666666666666668 9.98333

In [ ]:
# select features that we will actually use
final_join = all_data.groupBy(
                 "table1.AIRPORT_TIMEZONE",
                 "table1.src_lat",
                 "table1.src_long",             
                 "table1.TAIL_NUM", 
                 "table1.OP_UNIQUE_CARRIER",
                 "table1.FL_DATE",
                 "table1.ORIGIN_TIMESTAMP",
                 "table1.ORIGIN_TIMESTAMP2",
                 "table1.YEAR",
                 "table1.QUARTER",
                 "table1.MONTH",
                 "table1.DAY_OF_MONTH",
                 "table1.DAY_OF_WEEK",
                 "table1.ORIGIN",
                 "table1.DEST",
                 "table1.CRS_DEP_TIME",
                "table1.CRS_ELAPSED_TIME",
                "table1.DEST_AIRPORT_ID",
                "table1.OP_CARRIER",
                "table1.OP_CARRIER_FL_NUM",
                "table1.DEP_TIME_BLK",
                "table1.ARR_TIME_BLK",
                "table1.CRS_ARR_TIME",
                "table1.DEP_DEL15",
                "table1.CANCELLED",
                "table1.DEP_DELAY",
                "table1.ORIGIN_AIRPORT_ID",
                'table1.DepartureUTC',
                'table1.DepartureUTC2',
                'table1.airportDelayed',
                'table1.timeStartDelayed',
                "table1.avg_DryBulbTemp",
                'table1.avg_RelativeHumidity',
                'table1.avg_Visibility',
                'table1.avg_WindDirection',
                'table1.avg_WindSpeed'
                ) \
     .agg(count('table2.ORIGIN').alias("countDelaySameAirportDay"))
#                  

In [ ]:
final_join.display()

AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID DepartureUTC DepartureUTC2 airportDelayed timeStartDelayed avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed countDelaySameAirportDay America/New_York 40.65236278 -75.44040167 N416SW OO 2015-03-06 2015-03-06T16:00:00.000+0000 2015-03-06T14:00:00.000+0000 2015 1 3 6 5 ABE ATL 1600 128.0 10397 OO 4690 1600-1659 1800-1859 1808 0.0 0.0 -4.0 10135 2015-03-06T21:00:00.000+0000 2015-03-06T19:00:00.000+0000 notDelayed null 11.647058823529411 56.470588235294116 9.989411764705881 191.76470588235293 4.588235294117647 0 America/New_York 40.65236278 -75.44040167 N986AT DL 2015-03-06 2015-03-06T06:40:00.000+0000 2015-03-06T04:40:00.000+0000 2015 1 3 6 5 ABE ATL 640 128.0 10397 DL 2561 0600-0659 0800-0859 848 0.0 0.0 2.0 10135 2015-03-06T11:40:00.000+0000 2015-03-06T09:40:00.000+0000 notDelayed null 9.8 57.2 9.988 268.0 7.0 1 America/New_York 40.65236278 -75.44040167 N883AS EV 2015-03-06 2015-03-06T12:02:00.000+0000 2015-03-06T10:02:00.000+0000 2015 1 3 6 5 ABE ATL 1202 128.0 10397 EV 5041 1200-1259 1400-1459 1410 0.0 0.0 -5.0 10135 2015-03-06T17:02:00.000+0000 2015-03-06T15:02:00.000+0000 notDelayed null 8.166666666666666 60.833333333333336 9.99 235.0 5.416666666666667 0 America/New_York 40.65236278 -75.44040167 N933EV EV 2015-03-06 2015-03-06T13:00:00.000+0000 2015-03-06T11:00:00.000+0000 2015 1 3 6 5 ABE DTW 1300 107.0 11433 EV 4878 1300-1359 1400-1459 1447 1.0 0.0 58.0 10135 2015-03-06T18:00:00.000+0000 2015-03-06T16:00:00.000+0000 ABE 2015-03-06T18:00:00.000+0000 8.923076923076923 59.76923076923077 9.99076923076923 216.92307692307693 5.0 0 America/New_York 40.65236278 -75.44040167 N12563 EV 2015-03-06 2015-03-06T16:48:00.000+0000 2015-03-06T14:48:00.000+0000 2015 1 3 6 5 ABE ORD 1648 137.0 13930 EV 6144 1600-1659 1800-1859 1805 0.0 0.0 2.0 10135 2015-03-06T21:48:00.000+0000 2015-03-06T19:48:00.000+0000 notDelayed null 11.647058823529411 56.470588235294116 9.989411764705881 191.76470588235293 4.588235294117647 0 America/New_York 40.65236278 -75.44040167 N883AS EV 2015-03-06 2015-03-06T17:18:00.000+0000 2015-03-06T15:18:00.000+0000 2015 1 3 6 5 ABE DTW 1718 107.0 11433 EV 4963 1700-1759 1900-1959 1905 0.0 0.0 -1.0 10135 2015-03-06T22:18:00.000+0000 2015-03-06T20:18:00.000+0000 notDelayed null 12.222222222222221 55.888888888888886 9.99 192.22222222222223 4.611111111111111 0 America/New_York 40.65236278 -75.44040167 N857AS EV 2015-03-06 2015-03-06T06:00:00.000+0000 2015-03-06T04:00:00.000+0000 2015 1 3 6 5 ABE DTW 600 106.0 11433 EV 5302 0600-0659 0700-0759 746 0.0 0.0 -3.0 10135 2015-03-06T11:00:00.000+0000 2015-03-06T09:00:00.000+0000 notDelayed null 9.8 57.2 9.988 268.0 7.0 1 America/New_York 40.65236278 -75.44040167 N12135 EV 2015-03-06 2015-03-06T06:00:00.000+0000 2015-03-06T04:00:00.000+0000 2015 1 3 6 5 ABE ORD 600 140.0 13930 EV 6021 0600-0659 0700-0759 720 0.0 0.0 4.0 10135 2015-03-06T11:00:00.000+0000 2015-03-06T09:00:00.000+0000 notDelayed null 9.8 57.2 9.988 268.0 7.0 1 America/New_York 40.65236278 -75.44040167 N917EV EV 2015-07-09 2015-07-09T12:58:00.000+0000 2015-07-09T10:58:00.000+0000 2015 3 7 9 4 ABE DTW 1258 101.0 11433 EV 5050 1200-1259 1400-1459 1439 1.0 0.0 99.0 10135 2015-07-09T16:58:00.000+0000 2015-07-09T14:58:00.000+0000 ABE 2015-07-09T16:58:00.000+0000 70.625 85.20833333333333 7.7058333333333335 74.58333333333333 2.5 1 America/New_York 40.65236278 -75.44040167 N936EV EV 2015-07-09 2015-07-09T06:00:00.000+0000 2015-07-09T04:00:00.000+0000 2015 3 7 9 4 ABE DTW 600 100.0 11433 EV 4949 0600-0659 0700-0759 740 0.0 0.0 -4.0 10135 2015-07-09T10:00:00.000+0000 2015-07-09T08:00:00.000+0000 notDelayed null 71.0 83.71428571428571 9.562857142857142 127.14285714285714 4.85714285

In [ ]:
# save to blob
final_join.write.mode("overwrite").parquet(f"{store_blob_url}/featEngDelay")

In [ ]:
featEng = spark.read.parquet(f"{store_blob_url}/featEngDelay")

##Deriving Seasonality/Holiday Variable
* Our expectation is that in the major holidays of the year: Halloween, Thanksgiving, New Year's, Christmas break there would be significantly more traveling going on. The more people that travel, the more likelihood of a delay.

In [ ]:
#Create dictionary/list of US holidays from 2015-2021

#Holidays that don't vary from year to year, not used
general_holidays = {"New Year's Day" : '1-1', "Independence Day" : '7-4', "Veteran's Day": '11-4',	"Christmas Day" : '12-25'}
general_holidays_list = ['1-1', '7-4', '11-4', '12-25']

#Full Holiday list
holidays_list = ['7-4-2015','7-4-2016','7-4-2017','7-4-2018','7-4-2019','7-4-2020','7-4-2021','12-25-2015','12-25-2016','12-25-2017','12-25-2018','12-25-2019','12-25-2020','12-25-2021','12-24-2015','12-24-2016','12-24-2017','12-24-2018','12-24-2019','12-24-2020','12-24-2021','10-8-2018','10-9-2017','10-10-2016','10-11-2021','10-12-2015','10-12-2020','10-14-2019','4-8-2018','4-12-2015','4-16-2017','4-19-2020','4-28-2019','5-2-2021','5-1-2016','6-19-2020','6-19-2021','6-19-2015','6-19-2016','6-19-2017','6-19-2018','6-19-2019','9-2-2019','9-3-2018','9-4-2017','9-5-2016','9-6-2021','9-7-2015','9-7-2020','9-31-2019','9-1-2019','9-1-2018','9-2-2018','9-2-2017','9-3-2017','9-3-2016','9-4-2016','9-4-2021','9-5-2021','9-5-2015','9-5-2020','9-6-2015','9-6-2020','1-15-2018','1-16-2017','1-18-2016','1-18-2021','1-19-2015','1-20-2020','1-21-2019','5-25-2015','5-25-2020','5-27-2019','5-28-2018','5-29-2017','5-30-2016','5-31-2021','1-1-2015','1-1-2016','1-1-2017','1-1-2018','1-1-2019','1-1-2020','1-1-2021','12-31-2015','12-31-2016','12-31-2017','12-31-2018','12-31-2019','12-31-2020','12-31-2021','11-22-2018','11-23-2017','11-24-2016','11-25-2021','11-26-2015','11-26-2020','11-28-2019','11-21-2018','11-22-2017','11-23-2016','11-24-2021','11-25-2015','11-25-2020','11-27-2019','2-14-2015','2-14-2016','2-14-2017','2-14-2018','2-14-2019','2-14-2020','2-14-2021','11-11-2015','11-11-2016','11-11-2017','11-11-2018','11-11-2019','11-11-2020','11-11-2021','2-15-2016','2-16-2015','2-17-2020','2-18-2019','2-19-2018','2-20-2017','2-15-2021','3-27-2016','4-1-2018','4-4-2021','4-5-2015','4-12-2020','4-16-2017','4-21-2019']

holiday_list_3dayrange = ['7-1-2015','7-1-2016','7-1-2017','7-1-2018','7-1-2019','7-1-2020','7-1-2021','12-22-2015','12-22-2016','12-22-2017','12-22-2018','12-22-2019','12-22-2020','12-22-2021','12-21-2015','12-21-2016','12-21-2017','12-21-2018','12-21-2019','12-21-2020','12-21-2021','10-5-2018','10-6-2017','10-7-2016','10-8-2021','10-9-2015','10-9-2020','10-11-2019','4-5-2018','4-9-2015','4-13-2017','4-16-2020','4-25-2019','4-29-2021','4-28-2016','6-16-2020','6-16-2021','6-16-2015','6-16-2016','6-16-2017','6-16-2018','6-16-2019','8-30-2019','8-31-2018','9-1-2017','9-2-2016','9-3-2021','9-4-2015','9-4-2020','8-28-2019','8-29-2019','8-29-2018','8-30-2018','8-30-2017','8-31-2017','8-31-2016','9-1-2016','9-1-2021','9-2-2021','9-2-2015','9-2-2020','9-3-2015','9-3-2020','1-12-2018','1-13-2017','1-15-2016','1-15-2021','1-16-2015','1-17-2020','1-18-2019','5-22-2015','5-22-2020','5-24-2019','5-25-2018','5-26-2017','5-27-2016','5-28-2021','12-29-2014','12-29-2015','12-29-2016','12-29-2017','12-29-2018','12-29-2019','12-29-2020','12-28-2015','12-28-2016','12-28-2017','12-28-2018','12-28-2019','12-28-2020','12-28-2021','11-19-2018','11-20-2017','11-21-2016','11-22-2021','11-23-2015','11-23-2020','11-25-2019','11-18-2018','11-19-2017','11-20-2016','11-21-2021','11-22-2015','11-22-2020','11-24-2019','2-11-2015','2-11-2016','2-11-2017','2-11-2018','2-11-2019','2-11-2020','2-11-2021','11-8-2015','11-8-2016','11-8-2017','11-8-2018','11-8-2019','11-8-2020','11-8-2021','2-12-2016','2-13-2015','2-14-2020','2-15-2019','2-16-2018','2-17-2017','2-12-2021','3-24-2016','3-29-2018','4-1-2021','4-2-2015','4-9-2020','4-18-2019','7-2-2015','7-2-2016','7-2-2017','7-2-2018','7-2-2019','7-2-2020','7-2-2021','12-23-2015','12-23-2016','12-23-2017','12-23-2018','12-23-2019','12-23-2020','12-23-2021','10-6-2018','10-7-2017','10-8-2016','10-9-2021','10-10-2015','10-10-2020','10-12-2019','4-6-2018','4-10-2015','4-14-2017','4-17-2020','4-26-2019','4-30-2021','4-29-2016','6-17-2020','6-17-2021','6-17-2015','6-17-2016','6-17-2017','6-17-2018','6-17-2019','8-31-2019','9-1-2018','9-2-2017','9-3-2016','9-4-2021','9-5-2015','9-5-2020','1-13-2018','1-14-2017','1-16-2016','1-16-2021','1-17-2015','1-18-2020','1-19-2019','5-23-2015','5-23-2020','5-25-2019','5-26-2018','5-27-2017','5-28-2016','5-29-2021','12-30-2014','12-30-2015','12-30-2016','12-30-2017','12-30-2018','12-30-2019','12-30-2020','12-29-2021','11-20-2018','11-21-2017','11-22-2016','11-23-2021','11-24-2015','11-24-2020','11-26-2019','2-12-2015','2-12-2017','2-12-2018','2-12-2019','2-12-2020','11-9-2015','11-9-2016','11-9-2017','11-9-2018','11-9-2019','11-9-2020','11-9-2021','2-13-2016','2-14-2015','2-15-2020','2-16-2019','2-17-2018','2-18-2017','2-13-2021','3-25-2016','3-30-2018','4-2-2021','4-3-2015','4-10-2020','4-19-2019','7-3-2015','7-3-2016','7-3-2017','7-3-2018','7-3-2019','7-3-2020','7-3-2021','12-24-2015','12-24-2016','12-24-2017','12-24-2018','12-24-2019','12-24-2020','12-24-2021','10-7-2018','10-8-2017','10-9-2016','10-10-2021','10-11-2015','10-11-2020','10-13-2019','4-7-2018','4-11-2015','4-15-2017','4-18-2020','4-27-2019','5-1-2021','4-30-2016','6-18-2020','6-18-2021','6-18-2015','6-18-2016','6-18-2017','6-18-2018','6-18-2019','9-1-2019','9-2-2018','9-3-2017','9-4-2016','9-5-2021','9-6-2015','9-6-2020','1-14-2018','1-15-2017','1-17-2016','1-17-2021','1-18-2015','1-19-2020','1-20-2019','5-24-2015','5-24-2020','5-26-2019','5-27-2018','5-28-2017','5-29-2016','5-30-2021','12-31-2014','12-31-2015','12-31-2016','12-31-2017','12-31-2018','12-31-2019','12-31-2020','12-30-2021','11-21-2018','11-22-2017','11-23-2016','11-24-2021','11-25-2015','11-25-2020','11-27-2019','2-13-2017','2-13-2018','2-13-2019','2-13-2020','11-10-2015','11-10-2016','11-10-2017','11-10-2018','11-10-2019','11-10-2020','11-10-2021','2-14-2016','2-15-2015','2-16-2020','2-17-2019','2-18-2018','2-19-2017','2-14-2021','3-26-2016','3-31-2018','4-3-2021','4-4-2015','4-11-2020','4-20-2019','7-4-2015','7-4-2016','7-4-2017','7-4-2018','7-4-2019','7-4-2020','7-4-2021','12-25-2015','12-25-2016','12-25-2017','12-25-2018','12-25-2019','12-25-2020','12-25-2021','10-8-2018','10-9-2017','10-10-2016','10-11-2021','10-12-2015','10-12-2020','10-14-2019','4-8-2018','4-12-2015','4-16-2017','4-19-2020','4-28-2019','5-2-2021','5-1-2016','6-19-2020','6-19-2021','6-19-2015','6-19-2016','6-19-2017','6-19-2018','6-19-2019','9-2-2019','9-3-2018','9-4-2017','9-5-2016','9-6-2021','9-7-2015','9-7-2020','1-15-2018','1-16-2017','1-18-2016','1-18-2021','1-19-2015','1-20-2020','1-21-2019','5-25-2015','5-25-2020','5-27-2019','5-28-2018','5-29-2017','5-30-2016','5-31-2021','1-1-2015','1-1-2016','1-1-2017','1-1-2018','1-1-2019','1-1-2020','1-1-2021','12-31-2021','11-22-2018','11-23-2017','11-24-2016','11-25-2021','11-26-2015','11-26-2020','11-28-2019','2-14-2017','2-14-2018','2-14-2019','11-11-2015','11-11-2016','11-11-2017','11-11-2018','11-11-2019','11-11-2020','11-11-2021','2-15-2016','2-16-2015','2-17-2020','2-18-2019','2-19-2018','2-20-2017','2-15-2021','3-27-2016','4-1-2018','4-4-2021','4-5-2015','4-12-2020','4-21-2019','7-5-2015','7-5-2016','7-5-2017','7-5-2018','7-5-2019','7-5-2020','7-5-2021','12-26-2015','12-26-2016','12-26-2017','12-26-2018','12-26-2019','12-26-2020','12-26-2021','10-9-2018','10-10-2017','10-11-2016','10-12-2021','10-13-2015','10-13-2020','10-15-2019','4-9-2018','4-13-2015','4-17-2017','4-20-2020','4-29-2019','5-3-2021','5-2-2016','6-20-2020','6-20-2021','6-20-2015','6-20-2016','6-20-2017','6-20-2018','6-20-2019','9-3-2019','9-4-2018','9-5-2017','9-6-2016','9-7-2021','9-8-2015','9-8-2020','1-16-2018','1-17-2017','1-19-2016','1-19-2021','1-20-2015','1-21-2020','1-22-2019','5-26-2015','5-26-2020','5-28-2019','5-29-2018','5-30-2017','5-31-2016','6-1-2021','1-2-2015','1-2-2016','1-2-2017','1-2-2018','1-2-2019','1-2-2020','1-2-2021','1-1-2022','11-23-2018','11-24-2017','11-25-2016','11-26-2021','11-27-2015','11-27-2020','11-29-2019','2-15-2017','2-15-2018','11-12-2015','11-12-2016','11-12-2017','11-12-2018','11-12-2019','11-12-2020','11-12-2021','2-16-2016','2-17-2015','2-18-2020','2-19-2019','2-20-2018','2-21-2017','2-16-2021','3-28-2016','4-2-2018','4-5-2021','4-6-2015','4-13-2020','4-22-2019','7-6-2015','7-6-2016','7-6-2017','7-6-2018','7-6-2019','7-6-2020','7-6-2021','12-27-2015','12-27-2016','12-27-2017','12-27-2018','12-27-2019','12-27-2020','12-27-2021','10-10-2018','10-11-2017','10-12-2016','10-13-2021','10-14-2015','10-14-2020','10-16-2019','4-10-2018','4-14-2015','4-18-2017','4-21-2020','4-30-2019','5-4-2021','5-3-2016','6-21-2020','6-21-2021','6-21-2015','6-21-2016','6-21-2017','6-21-2018','6-21-2019','9-4-2019','9-5-2018','9-6-2017','9-7-2016','9-8-2021','9-9-2015','9-9-2020','1-17-2018','1-18-2017','1-20-2016','1-20-2021','1-21-2015','1-22-2020','1-23-2019','5-27-2015','5-27-2020','5-29-2019','5-30-2018','5-31-2017','6-1-2016','6-2-2021','1-3-2015','1-3-2016','1-3-2017','1-3-2018','1-3-2019','1-3-2020','1-3-2021','1-2-2022','11-24-2018','11-25-2017','11-26-2016','11-27-2021','11-28-2015','11-28-2020','11-30-2019','2-16-2017','11-13-2015','11-13-2016','11-13-2017','11-13-2018','11-13-2019','11-13-2020','11-13-2021','2-17-2016','2-18-2015','2-19-2020','2-20-2019','2-21-2018','2-22-2017','2-17-2021','3-29-2016','4-3-2018','4-6-2021','4-7-2015','4-14-2020','4-23-2019','7-7-2015','7-7-2016','7-7-2017','7-7-2018','7-7-2019','7-7-2020','7-7-2021','10-11-2018','10-12-2017','10-13-2016','10-14-2021','10-15-2015','10-15-2020','10-17-2019','4-11-2018','4-15-2015','4-19-2017','4-22-2020','5-1-2019','5-5-2021','5-4-2016','6-22-2020','6-22-2021','6-22-2015','6-22-2016','6-22-2017','6-22-2018','6-22-2019','9-5-2019','9-6-2018','9-7-2017','9-8-2016','9-9-2021','9-10-2015','9-10-2020','1-18-2018','1-19-2017','1-21-2016','1-21-2021','1-22-2015','1-23-2020','1-24-2019','5-28-2015','5-28-2020','5-30-2019','5-31-2018','6-1-2017','6-2-2016','6-3-2021','1-4-2015','1-4-2016','1-4-2017','1-4-2018','1-4-2019','1-4-2020','1-4-2021','1-3-2022','11-25-2018','11-26-2017','11-27-2016','11-28-2021','11-29-2015','11-29-2020','12-1-2019','11-14-2015','11-14-2016','11-14-2017','11-14-2018','11-14-2019','11-14-2020','11-14-2021','2-18-2016','2-19-2015','2-20-2020','2-21-2019','2-22-2018','2-23-2017','2-18-2021','3-30-2016','4-4-2018','4-7-2021','4-8-2015','4-15-2020','4-24-2019']


In [ ]:
#Create a new column that is a concatentation of month, and day of month, and year columns to compare against holiday column
featEng_hol = featEng.withColumn('month_day_year', 
                    F.concat(F.col('MONTH'),F.lit('-'), F.col('DAY_OF_MONTH'), F.lit('-'),F.col('YEAR')))


In [ ]:
#Create new variable 'Holiday_Flag' flagging when the date falls on a holiday, '1' is a holiday, '0' is not a holiday
featEng_hol = featEng_hol.withColumn('Holiday_Flag', F.when(col('month_day_year').isin(holidays_list), 1).otherwise(0))

featEng_hol = featEng_hol.withColumn('Holiday_Flag_3dayrange', F.when(col('month_day_year').isin(holiday_list_3dayrange), 1).otherwise(0))

display(featEng_hol)

AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID DepartureUTC DepartureUTC2 airportDelayed timeStartDelayed avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed countDelaySameAirportDay month_day_year Holiday_Flag Holiday_Flag_3dayrange America/New_York 40.65236278 -75.44040167 N27152 EV 2015-05-02 2015-05-02T06:36:00.000+0000 2015-05-02T04:36:00.000+0000 2015 2 5 2 6 ABE ORD 636 129.0 13930 EV 6021 0600-0659 0700-0759 745 0.0 0.0 -8.0 10135 2015-05-02T10:36:00.000+0000 2015-05-02T08:36:00.000+0000 notDelayed null 47.0 78.6 9.988 44.0 2.0 0 5-2-2015 0 0 America/New_York 40.65236278 -75.44040167 N923EV EV 2015-05-02 2015-05-02T14:00:00.000+0000 2015-05-02T12:00:00.000+0000 2015 2 5 2 6 ABE ATL 1400 127.0 10397 EV 5033 1400-1459 1600-1659 1607 0.0 0.0 -8.0 10135 2015-05-02T18:00:00.000+0000 2015-05-02T16:00:00.000+0000 notDelayed null 53.285714285714285 68.92857142857143 9.991428571428571 41.42857142857143 1.1428571428571428 0 5-2-2015 0 0 America/New_York 40.65236278 -75.44040167 N914EV EV 2015-05-02 2015-05-02T09:25:00.000+0000 2015-05-02T07:25:00.000+0000 2015 2 5 2 6 ABE DTW 925 101.0 11433 EV 5116 0900-0959 1100-1159 1106 0.0 0.0 5.0 10135 2015-05-02T13:25:00.000+0000 2015-05-02T11:25:00.000+0000 notDelayed null 47.44444444444444 78.88888888888889 9.986666666666666 24.444444444444443 1.1111111111111112 0 5-2-2015 0 0 America/New_York 40.65236278 -75.44040167 N933AT DL 2015-05-02 2015-05-02T06:40:00.000+0000 2015-05-02T04:40:00.000+0000 2015 2 5 2 6 ABE ATL 640 125.0 10397 DL 2561 0600-0659 0800-0859 845 0.0 0.0 -2.0 10135 2015-05-02T10:40:00.000+0000 2015-05-02T08:40:00.000+0000 notDelayed null 47.0 78.6 9.988 44.0 2.0 0 5-2-2015 0 0 America/New_York 40.65236278 -75.44040167 N921EV EV 2015-06-11 2015-06-11T17:17:00.000+0000 2015-06-11T15:17:00.000+0000 2015 2 6 11 4 ABE DTW 1717 98.0 11433 EV 4891 1700-1759 1800-1859 1855 1.0 0.0 21.0 10135 2015-06-11T21:17:00.000+0000 2015-06-11T19:17:00.000+0000 ABE 2015-06-11T21:17:00.000+0000 76.22222222222223 68.94444444444444 6.472777777777778 205.55555555555554 6.388888888888889 0 6-11-2015 0 0 America/New_York 40.65236278 -75.44040167 N853AS EV 2015-06-11 2015-06-11T06:00:00.000+0000 2015-06-11T04:00:00.000+0000 2015 2 6 11 4 ABE DTW 600 100.0 11433 EV 5251 0600-0659 0700-0759 740 0.0 0.0 -4.0 10135 2015-06-11T10:00:00.000+0000 2015-06-11T08:00:00.000+0000 notDelayed null 67.4 78.4 7.94 202.0 3.6 3 6-11-2015 0 0 America/New_York 40.65236278 -75.44040167 N881AS EV 2015-06-11 2015-06-11T16:00:00.000+0000 2015-06-11T14:00:00.000+0000 2015 2 6 11 4 ABE ATL 1600 131.0 10397 EV 4940 1600-1659 1800-1859 1811 0.0 0.0 -2.0 10135 2015-06-11T20:00:00.000+0000 2015-06-11T18:00:00.000+0000 notDelayed null 75.47058823529412 69.88235294117646 6.4417647058823535 202.94117647058823 6.117647058823529 0 6-11-2015 0 0 America/New_York 40.65236278 -75.44040167 N12552 EV 2015-06-11 2015-06-11T11:35:00.000+0000 2015-06-11T09:35:00.000+0000 2015 2 6 11 4 ABE ORD 1135 129.0 13930 EV 6011 1100-1159 1200-1259 1244 0.0 0.0 -8.0 10135 2015-06-11T15:35:00.000+0000 2015-06-11T13:35:00.000+0000 notDelayed null 70.0 77.0909090909091 6.424545454545455 179.0909090909091 4.090909090909091 1 6-11-2015 0 0 America/New_York 40.65236278 -75.44040167 N14907 EV 2015-06-11 2015-06-11T06:27:00.000+0000 2015-06-11T04:27:00.000+0000 2015 2 6 11 4 ABE ORD 627 123.0 13930 EV 6021 0600-0659 0700-0759 730 0.0 0.0 -6.0 10135 2015-06-11T10:27:00.000+0000 2015-06-11T08:27:00.000+0000 notDelayed null 67.4 78.4 7.94 202.0 3.6 3 6-11-2015 0 0 America/New_York 40.65236278 -75.44040167 N855AS EV 2015-06-11 2015-06-11T13:05:00.000+0000 2015-06-11T11:05:00.000+0000 2015 2 6 11 4 ABE DTW 1305 101.0 11433 EV 5050 1300-1359 1400-1459 1446 1.0 0.0

Output can only be rendered in Databricks

In [ ]:
#Test for when holiday_flag is TRUE
display(featEng_hol.filter(featEng_hol.Holiday_Flag == 1))

AIRPORT_TIMEZONE src_lat src_long TAIL_NUM OP_UNIQUE_CARRIER FL_DATE ORIGIN_TIMESTAMP ORIGIN_TIMESTAMP2 YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK ORIGIN DEST CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID OP_CARRIER OP_CARRIER_FL_NUM DEP_TIME_BLK ARR_TIME_BLK CRS_ARR_TIME DEP_DEL15 CANCELLED DEP_DELAY ORIGIN_AIRPORT_ID DepartureUTC DepartureUTC2 airportDelayed timeStartDelayed avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed countDelaySameAirportDay month_day_year Holiday_Flag Holiday_Flag_3dayrange America/New_York 40.65236278 -75.44040167 402NV G4 2018-10-08 2018-10-08T15:47:00.000+0000 2018-10-08T13:47:00.000+0000 2018 4 10 8 1 ABE SFB 1547 150.0 14761 G4 2125 1500-1559 1800-1859 1817 0.0 0.0 -9.0 10135 2018-10-08T19:47:00.000+0000 2018-10-08T17:47:00.000+0000 notDelayed null 67.34782608695652 86.65217391304348 5.718260869565216 70.0 7.6521739130434785 0 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 402NV G4 2018-10-08 2018-10-08T11:08:00.000+0000 2018-10-08T09:08:00.000+0000 2018 4 10 8 1 ABE MYR 1108 91.0 13577 G4 2272 1100-1159 1200-1259 1239 0.0 0.0 -5.0 10135 2018-10-08T15:08:00.000+0000 2018-10-08T13:08:00.000+0000 notDelayed null 67.2 86.53333333333333 7.652 65.33333333333333 7.866666666666666 1 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N903XJ 9E 2018-10-08 2018-10-08T18:05:00.000+0000 2018-10-08T16:05:00.000+0000 2018 4 10 8 1 ABE ATL 1805 127.0 10397 9E 3324 1800-1859 2000-2059 2012 0.0 0.0 -8.0 10135 2018-10-08T22:05:00.000+0000 2018-10-08T20:05:00.000+0000 notDelayed null 67.5 86.71428571428571 5.482857142857143 75.0 7.821428571428571 0 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N956AT DL 2018-10-08 2018-10-08T06:00:00.000+0000 2018-10-08T04:00:00.000+0000 2018 4 10 8 1 ABE ATL 600 125.0 10397 DL 2772 0600-0659 0800-0859 805 0.0 0.0 -1.0 10135 2018-10-08T10:00:00.000+0000 2018-10-08T08:00:00.000+0000 notDelayed null 69.57142857142857 87.57142857142857 8.54857142857143 68.57142857142857 7.857142857142857 2 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N596NN OH 2018-10-08 2018-10-08T11:43:00.000+0000 2018-10-08T09:43:00.000+0000 2018 4 10 8 1 ABE CLT 1143 124.0 11057 OH 5314 1100-1159 1300-1359 1347 0.0 0.0 -11.0 10135 2018-10-08T15:43:00.000+0000 2018-10-08T13:43:00.000+0000 notDelayed null 67.2 86.53333333333333 7.652 65.33333333333333 7.866666666666666 1 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N589NN OH 2018-10-08 2018-10-08T16:49:00.000+0000 2018-10-08T14:49:00.000+0000 2018 4 10 8 1 ABE CLT 1649 132.0 11057 OH 5231 1600-1659 1900-1959 1901 1.0 0.0 16.0 10135 2018-10-08T20:49:00.000+0000 2018-10-08T18:49:00.000+0000 ABE 2018-10-08T20:49:00.000+0000 67.44 86.68 5.540799999999999 72.0 7.72 0 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N418SW OO 2018-10-08 2018-10-08T17:31:00.000+0000 2018-10-08T15:31:00.000+0000 2018 4 10 8 1 ABE DTW 1731 110.0 11433 OO 4303 1700-1759 1900-1959 1921 0.0 0.0 -1.0 10135 2018-10-08T21:31:00.000+0000 2018-10-08T19:31:00.000+0000 notDelayed null 67.48148148148148 86.70370370370371 5.352592592592592 73.70370370370371 7.777777777777778 0 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N563NN OH 2018-10-08 2018-10-08T06:11:00.000+0000 2018-10-08T04:11:00.000+0000 2018 4 10 8 1 ABE CLT 611 124.0 11057 OH 5105 0600-0659 0800-0859 815 0.0 0.0 -10.0 10135 2018-10-08T10:11:00.000+0000 2018-10-08T08:11:00.000+0000 notDelayed null 69.57142857142857 87.57142857142857 8.54857142857143 68.57142857142857 7.857142857142857 2 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N538CA 9E 2018-10-08 2018-10-08T13:25:00.000+0000 2018-10-08T11:25:00.000+0000 2018 4 10 8 1 ABE ATL 1325 130.0 10397 9E 3329 1300-1359 1500-1559 1535 0.0 0.0 -5.0 10135 2018-10-08T17:25:00.000+0000 2018-10-08T15:25:00.000+0000 notDelayed null 67.0 86.83333333333333 6.640555555555555 63.333333333333336 7.555555555555555 1 10-8-2018 1 1 America/New_York 40.65236278 -75.44040167 N944SW OO 2018-10-08 2018-10-

## Label encoder
* converting the carrier categorical variable to numeric so that the models can use this feature. We chose label encoder because it would save space on the encoding versus what the one-hot encoding would have needed.

In [ ]:
# somehow the read blob data type became string. Going to change this to be the previous type 

featEng_hol.registerTempTable("featEng_hol")


query =  '''
SELECT
 DepartureUTC,
 OP_UNIQUE_CARRIER,
 INT(YEAR),
 INT(QUARTER),
 INT(DAY_OF_WEEK),
 INT(CRS_DEP_TIME),
 DOUBLE(CRS_ELAPSED_TIME),
 INT(DEST_AIRPORT_ID),
 INT(ORIGIN_AIRPORT_ID),
 INT(OP_CARRIER_FL_NUM),
 INT(CRS_ARR_TIME),
 INT(countDelaySameAirportDay),
 INT(Holiday_Flag),
 INT(Holiday_Flag_3dayrange),
 DOUBLE(DEP_DELAY),
 DOUBLE(avg_DryBulbTemp),
 DOUBLE(avg_RelativeHumidity),
 DOUBLE(avg_Visibility),
 DOUBLE(avg_WindDirection),
 DOUBLE(avg_WindSpeed)
 
 FROM featEng_hol
 '''

#  'DEP_DELAY' is the predicted variable

modelData = spark.sql(query)

/databricks/spark/python/pyspark/sql/dataframe.py:234: FutureWarning: Deprecated in 2.0, use createOrReplaceTempView instead.
  warnings.warn("Deprecated in 2.0, use createOrReplaceTempView instead.", FutureWarning)


In [ ]:
def categorical_indexer(origCatCol, outputColName, df ):
    '''
    this function label indexes the input categorical variable and drops the original categorical variable column from the dataframe
    
    origCatCol - string; column name of the categorical variable
    outputColName - string; desired output column name of the indexed categorical variable
    df - the dataframe holding all the input features including the categorical variable you would like to index
    '''
    
    indexer = StringIndexer(inputCol=origCatCol, outputCol=outputColName) 
    df = indexer.fit(df).transform(df) 
    
    # drop the original categorical columns, only want to keep the label-encoded ones
    cat_col = [origCatCol]
    df = df.drop(*cat_col)
    
    return df
    

In [ ]:
modelData = categorical_indexer('OP_UNIQUE_CARRIER', 'OP_UNIQUE_CARRIERIndex', modelData )

In [ ]:
modelData.display()

DepartureUTC YEAR QUARTER DAY_OF_WEEK CRS_DEP_TIME CRS_ELAPSED_TIME DEST_AIRPORT_ID ORIGIN_AIRPORT_ID OP_CARRIER_FL_NUM CRS_ARR_TIME countDelaySameAirportDay Holiday_Flag Holiday_Flag_3dayrange DEP_DELAY avg_DryBulbTemp avg_RelativeHumidity avg_Visibility avg_WindDirection avg_WindSpeed OP_UNIQUE_CARRIERIndex 2015-05-02T10:36:00.000+0000 2015 2 6 636 129.0 13930 10135 6021 745 0 0 0 -8.0 47.0 78.6 9.988 44.0 2.0 6.0 2015-05-02T18:00:00.000+0000 2015 2 6 1400 127.0 10397 10135 5033 1607 0 0 0 -8.0 53.285714285714285 68.92857142857143 9.991428571428571 41.42857142857143 1.1428571428571428 6.0 2015-05-02T13:25:00.000+0000 2015 2 6 925 101.0 11433 10135 5116 1106 0 0 0 5.0 47.44444444444444 78.88888888888889 9.986666666666666 24.444444444444443 1.1111111111111112 6.0 2015-05-02T10:40:00.000+0000 2015 2 6 640 125.0 10397 10135 2561 845 0 0 0 -2.0 47.0 78.6 9.988 44.0 2.0 1.0 2015-06-11T21:17:00.000+0000 2015 2 4 1717 98.0 11433 10135 4891 1855 0 0 0 21.0 76.22222222222223 68.94444444444444 6.472777777777778 205.55555555555554 6.388888888888889 6.0 2015-06-11T10:00:00.000+0000 2015 2 4 600 100.0 11433 10135 5251 740 3 0 0 -4.0 67.4 78.4 7.94 202.0 3.6 6.0 2015-06-11T20:00:00.000+0000 2015 2 4 1600 131.0 10397 10135 4940 1811 0 0 0 -2.0 75.47058823529412 69.88235294117646 6.4417647058823535 202.94117647058823 6.117647058823529 6.0 2015-06-11T15:35:00.000+0000 2015 2 4 1135 129.0 13930 10135 6011 1244 1 0 0 -8.0 70.0 77.0909090909091 6.424545454545455 179.0909090909091 4.090909090909091 6.0 2015-06-11T10:27:00.000+0000 2015 2 4 627 123.0 13930 10135 6021 730 3 0 0 -6.0 67.4 78.4 7.94 202.0 3.6 6.0 2015-06-11T17:05:00.000+0000 2015 2 4 1305 101.0 11433 10135 5050 1446 1 0 0 48.0 72.07692307692308 74.3076923076923 6.359230769230769 190.0 4.846153846153846 6.0 2015-06-11T10:15:00.000+0000 2015 2 4 615 119.0 10397 10135 2556 814 3 0 0 -6.0 67.4 78.4 7.94 202.0 3.6 1.0 2015-06-11T16:02:00.000+0000 2015 2 4 1202 128.0 10397 10135 5033 1410 1 0 0 16.0 71.08333333333333 75.58333333333333 6.389166666666667 184.16666666666666 4.5 6.0 2016-04-20T21:44:00.000+0000 2016 2 3 1744 136.0 13930 10135 3982 1900 0 0 0 -9.0 54.875 34.4375 9.98875 138.75 4.625 6.0 2016-04-20T17:01:00.000+0000 2016 2 3 1301 134.0 10397 10135 5540 1515 0 0 0 8.0 50.583333333333336 40.416666666666664 9.99 153.33333333333334 5.666666666666667 6.0 2016-04-20T21:32:00.000+0000 2016 2 3 1732 135.0 10397 10135 5267 1947 0 0 0 -7.0 54.875 34.4375 9.98875 138.75 4.625 6.0 2016-04-20T09:45:00.000+0000 2016 2 3 545 133.0 10397 10135 939 758 0 0 0 42.0 45.5 47.25 9.985 342.5 8.25 1.0 2016-04-20T10:00:00.000+0000 2016 2 3 600 136.0 13930 10135 3761 716 0 0 0 -6.0 45.6 47.0 9.988 344.0 8.0 6.0 2016-04-20T21:35:00.000+0000 2016 2 3 1735 105.0 11433 10135 4702 1920 0 0 0 -4.0 54.875 34.4375 9.98875 138.75 4.625 3.0 2016-05-15T16:42:00.000+0000 2016 2 7 1242 104.0 11433 10135 4537 1426 0 0 0 -3.0 48.0 62.714285714285715 9.991428571428571 276.42857142857144 11.071428571428571 3.0 2016-05-15T09:46:00.000+0000 2016 2 7 546 126.0 10397 10135 2561 752 0 0 0 -2.0 46.5 61.25 9.985 272.5 7.0 1.0 2016-05-15T21:11:00.000+0000 2016 2 7 1711 136.0 13930 10135 3982 1827 0 0 0 2.0 49.25 59.7 9.991 270.5 12.95 6.0 2016-05-15T17:16:00.000+0000 2016 2 7 1316 128.0 10397 10135 5415 1524 0 0 0 0.0 48.266666666666666 61.53333333333333 9.991999999999999 275.3333333333333 11.333333333333334 6.0 2016-05-15T21:55:00.000+0000 2016 2 7 1755 104.0 11433 10135 5130 1939 0 0 0 -5.0 49.04761904761905 60.23809523809524 9.991428571428571 270.4761904761905 13.0 6.0 2016-05-15T21:55:00.000+0000 2016 2 7 1755 129.0 10397 10135 5427 2004 0 0 0 -7.0 49.04761904761905 60.23809523809524 9.991428571428571 270.4761904761905 13.0 6.0 2016-05-15T10:45:00.000+0000 2016 2 7 645 136.0 13930 10135 3761 801 0 0 0 -6.0 46.0 63.2 9.988 268.0 6.8 6.0 2016-07-07T10:00:00.000+0000 2016 3 4 600 120.0 10397 10135 551 800 1 0 1 -3.0 71.8 86.4 8.788 0.0 0.0 1.0 2016-07-07T22:10:00.000+0000 2016 3 4 1810 131.0 10397 10135 5367 2021 0 0 1 8.0 79.5

In [ ]:
# save to blob checkpoint
modelData.write.mode("overwrite").parquet(f"{store_blob_url}/modelData")

In [ ]:
modelData.count()

Out[51]: 40994727

###note: modelData has been updated to include the weather on Dec 1

In [ ]:
#read the checkpoint
modelDataC = spark.read.parquet(f"{store_blob_url}/modelData")

In [ ]:
modelDataC.printSchema()

root
 |-- DepartureUTC: timestamp (nullable = true)
 |-- YEAR: integer (nullable = true)
 |-- QUARTER: integer (nullable = true)
 |-- DAY_OF_WEEK: integer (nullable = true)
 |-- CRS_DEP_TIME: integer (nullable = true)
 |-- CRS_ELAPSED_TIME: double (nullable = true)
 |-- DEST_AIRPORT_ID: integer (nullable = true)
 |-- ORIGIN_AIRPORT_ID: integer (nullable = true)
 |-- OP_CARRIER_FL_NUM: integer (nullable = true)
 |-- CRS_ARR_TIME: integer (nullable = true)
 |-- countDelaySameAirportDay: integer (nullable = true)
 |-- Holiday_Flag: integer (nullable = true)
 |-- Holiday_Flag_3dayrange: integer (nullable = true)
 |-- DEP_DELAY: double (nullable = true)
 |-- tailnumIndex: double (nullable = true)
 |-- OP_UNIQUE_CARRIERIndex: double (nullable = true)



In [ ]:
def get_subset(df, date_tuple):
    """ Get subset of a dataframe
    from provided dates"""
    
    dates = date_tuple

    timestamps = (
        time.mktime(datetime.datetime.strptime(s, "%Y-%m-%d %H:%M:%S").timetuple())
        for s in dates)

    q1 = "CAST(DepartureUTC AS INT) BETWEEN {0} AND {1}".format(*timestamps)
    df_out = df.where(q1)
    return df_out

In [ ]:
def SumAnnualDelays(inputdf):
    """ Sum all the delays from same airport 
    (source to departure) annually"""
    
    #create temporary tables for queries and joining
    inputdf.registerTempTable("inputdf")

    query = '''
    SELECT ORIGIN_AIRPORT_ID, SUM(countDelaySameAirportDay) AS RANK, DEST_AIRPORT_ID
    FROM inputdf
    GROUP BY ORIGIN_AIRPORT_ID, DEST_AIRPORT_ID
    ORDER BY ORIGIN_AIRPORT_ID, DEST_AIRPORT_ID
    '''

    all_data = spark.sql(query)
    return all_data

In [ ]:
def AppendPageRankOrigin(rank_df, indexed_df):
    """ Append Origin Pagerank back to the dataset that has
    Airport ID identifier """
    
    #create temporary tables for queries and joining
    rank_df.registerTempTable("rank")
    indexed_df.registerTempTable("index")

    query = '''
    SELECT DISTINCT index.ORIGIN_AIRPORT_ID, rank.Rank AS ORIGIN_PAGERANK
    FROM index
        LEFT JOIN rank ON rank.Airport_Index = index.srcIdIndex
    '''

    all_data = spark.sql(query)
    return all_data

In [ ]:
def ToOriginalDatasetPageRankOrigin(orginal, page_rank):
    """ Append Origin the pagerank to original dataset """
    
    #create temporary tables for queries and joining
    orginal.registerTempTable("original")
    page_rank.registerTempTable("rank")

    query = '''
    SELECT *
    FROM original
        LEFT JOIN rank ON original.ORIGIN_AIRPORT_ID = rank.ORIGIN_AIRPORT_ID
    '''

    all_data = spark.sql(query)
    return all_data

In [ ]:
def AppendPageRankDest(rank_df, indexed_df):
    """ Append Destination Pagerank back to the dataset that has
    Airport ID identifier """
    
    #create temporary tables for queries and joining
    rank_df.registerTempTable("rank")
    indexed_df.registerTempTable("index")

    query = '''
    SELECT DISTINCT index.DEST_AIRPORT_ID, rank.Rank AS DEST_PAGERANK
    FROM index
        LEFT JOIN rank ON rank.Airport_Index = index.destIdIndex
    '''

    all_data = spark.sql(query)
    return all_data

In [ ]:
def ToOriginalDatasetPageRankOriginDest(orginal, page_rank):
    """ Append Destination the pagerank to original dataset """
    
    #create temporary tables for queries and joining
    orginal.registerTempTable("original")
    page_rank.registerTempTable("rank")

    query = '''
    SELECT *
    FROM original
        LEFT JOIN rank ON original.DEST_AIRPORT_ID = rank.DEST_AIRPORT_ID
    '''

    all_data = spark.sql(query)
    return all_data

In [ ]:
def CreateAndAppendGraphFeature(dates, dates_next_year, data, shape):
    """ Index the airports, calculate airport, append back to the original dataset
     and remove duplicated columbs at the end
     dates: year we're calculating pagerank for
     dates_next_year: year we're appending the page rank to
     data: datagrame to work with
     shape: how many airports we indexed during that year"""
    
    year_data = get_subset(data, (dates))
    year_data_graph = year_data.select('ORIGIN_AIRPORT_ID', 'DEST_AIRPORT_ID', 'countDelaySameAirportDay')
    year_data_summed = SumAnnualDelays(year_data_graph)
    
    indexer = StringIndexer(inputCol="ORIGIN_AIRPORT_ID", outputCol="srcIdIndex") 
    year_data_indexed = indexer.fit(year_data_summed).transform(year_data_summed) 
    
    indexer = StringIndexer(inputCol="DEST_AIRPORT_ID", outputCol="destIdIndex") 
    year_data_indexed = indexer.fit(year_data_indexed).transform(year_data_indexed)
    
    np_year = year_data_indexed.toPandas().to_numpy()
    
    weights = np_year[:,1]
    G = sparse.csr_matrix((weights, (np_year[:,3].astype(int), np_year[:,4].astype(int))), shape = shape) #csr graph 
    pr=pagerank(G, p=0.85) # p is the damping factor 
    
    d = np.column_stack([range(0, shape[0]), pr])
    
    df = pd.DataFrame(d, columns=['Airport_Index', 'Rank'])
    
    pagerankid_data = spark.createDataFrame(df)
    
    df_year = AppendPageRankOrigin(pagerankid_data, year_data_indexed)
    
    data_next_year = get_subset(data, dates_next_year)
    
    next_year_with_rank = ToOriginalDatasetPageRankOrigin(data_next_year, df_year)
    
    df_year_dest = AppendPageRankDest(pagerankid_data, year_data_indexed)
    
    next_year_with_rank = ToOriginalDatasetPageRankOriginDest(next_year_with_rank, df_year_dest)
    
    # There is an additional duplicated column that need to be removed
    df = next_year_with_rank

    df_cols = df.columns
    # get index of the duplicate columns
    duplicate_col_index = list(set([df_cols.index(c) for c in df_cols if df_cols.count(c) == 2]))

    # rename by adding suffix '_duplicated'
    for i in duplicate_col_index:
        df_cols[i] = df_cols[i] + '_duplicated'

    # rename the column in DF
    df = df.toDF(*df_cols)

    # remove flagged columns
    cols_to_remove = [c for c in df_cols if '_duplicated' in c]
    df = df.drop(*cols_to_remove)
    
    return df

In [ ]:
def toOriginalDatasetNoPageRank(dates):
    """ Create pagerank columns with 0s for data that has no 
    previous pagerank value """
    
    year_data = get_subset(data, (dates))
    
    data_col = year_data.withColumn("ORIGIN_PAGERANK", lit(0.0))
    data_col = data_col.withColumn("DEST_PAGERANK", lit(0.0))
    
    return data_col

In [ ]:
data_with_graph_2016 = CreateAndAppendGraphFeature(("2015-01-01 00:00:00",  "2015-12-31 00:00:00"), ("2016-01-01 00:00:00",  "2016-12-31 00:00:00"), data, (320,320))
data_with_graph_2017 = CreateAndAppendGraphFeature(("2016-01-01 00:00:00",  "2016-12-31 00:00:00"), ("2017-01-01 00:00:00",  "2017-12-31 00:00:00"), data, (320,320))
data_with_graph_2018 = CreateAndAppendGraphFeature(("2017-01-01 00:00:00",  "2017-12-31 00:00:00"), ("2018-01-01 00:00:00",  "2018-12-31 00:00:00"), data, (320,320))
data_with_graph_2019 = CreateAndAppendGraphFeature(("2018-01-01 00:00:00",  "2018-12-31 00:00:00"), ("2019-01-01 00:00:00",  "2019-12-31 00:00:00"), data, (354,354))
data_with_graph_2020 = CreateAndAppendGraphFeature(("2019-01-01 00:00:00",  "2019-12-31 00:00:00"), ("2020-01-01 00:00:00",  "2020-12-31 00:00:00"), data, (355,355))
data_with_graph_2021 = CreateAndAppendGraphFeature(("2020-01-01 00:00:00",  "2020-12-31 00:00:00"), ("2021-01-01 00:00:00",  "2021-12-31 00:00:00"), data, (362,362))


data_with_graph_2015 = toOriginalDatasetNoPageRank(("2015-01-01 00:00:00",  "2015-12-31 00:00:00"))


df_full = data_with_graph_2015.unionByName(data_with_graph_2016)
df_full = df_full.unionByName(data_with_graph_2017)
df_full = df_full.unionByName(data_with_graph_2018)
df_full = df_full.unionByName(data_with_graph_2019)
df_full = df_full.unionByName(data_with_graph_2020)
df_full = df_full.unionByName(data_with_graph_2021)

df_full.display()

In [ ]:
df_full_nonull = df_full.na.drop()

In [ ]:
# df_full.write.mode("overwrite").parquet(f"{store_blob_url}/data_with_rank_2")